In [34]:
!pip install folium

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.0/100.0 kB 8.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.0/82.0 kB 11.8 MB/s eta 0:00:00


In [2]:
import boto3
import pandas as pd
from io import BytesIO
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
import folium

In [2]:
asn_df = pd.read_csv('GeoLite2-ASN-Blocks-IPv4.csv')
asn_df.head()

network  autonomous_system_number     autonomous_system_organization
0   1.0.0.0/24                     13335                      CLOUDFLARENET
1   1.0.4.0/22                     38803          Wirefreebroadband Pty Ltd
2  1.0.16.0/24                      2519       ARTERIA Networks Corporation
3  1.0.32.0/24                    141748  QUANTUM DATA COMMUNICATIONS, INC.
4  1.0.64.0/18                     18144                        Enecom,Inc.

In [3]:
city_df = pd.read_csv('GeoLite2-City-Blocks-IPv4.csv')
city_df

/tmp/ipykernel_30976/3067899796.py:1: DtypeWarning: Columns (6) have mixed types. Specify dtype option on import or set low_memory=False.
  city_df = pd.read_csv('GeoLite2-City-Blocks-IPv4.csv')


network  geoname_id  registered_country_geoname_id  \
0              1.0.0.0/24         NaN                      2077456.0   
1              1.0.1.0/24   1814991.0                      1814991.0   
2              1.0.2.0/23   1814991.0                      1814991.0   
3              1.0.4.0/22   2077456.0                      2077456.0   
4              1.0.8.0/21   1814991.0                      1814991.0   
...                   ...         ...                            ...   
2453530  223.255.247.0/24   1269750.0                      1269750.0   
2453531  223.255.248.0/22   1819729.0                      1819730.0   
2453532  223.255.252.0/23   1814991.0                      1814991.0   
2453533  223.255.254.0/24   1880251.0                      1880251.0   
2453534  223.255.255.0/24   2077456.0                      2077456.0   

         represented_country_geoname_id  is_anonymous_proxy  \
0                                   NaN                   0   
1                                   NaN                   0   
2                                   NaN                   0   
3                                   NaN                   0   
4                                   NaN                   0   
...                                 ...                 ...   
2453530                             NaN                   0   
2453531                             NaN                   0   
2453532                             NaN                   0   
2453533                             NaN                   0   
2453534                             NaN                   0   

         is_satellite_provider postal_code  latitude  longitude  \
0                            0         NaN       NaN        NaN   
1                            0         NaN   34.7732   113.7220   
2                            0         NaN   34.7732   113.7220   
3                            0         NaN  -33.4940   143.2104   
4                            0         NaN   34.7732   113.7220   
...                        ...         ...       ...        ...   
2453530                      0         NaN   21.9974    79.0011   
2453531                      0         NaN   22.2842   114.1759   
2453532                      0         NaN   34.7732   113.7220   
2453533                      0         NaN    1.3673   103.8014   
2453534                      0         NaN  -33.4940   143.2104   

         accuracy_radius  is_anycast  
0                    NaN         NaN  
1                 1000.0         NaN  
2                 1000.0         NaN  
3                 1000.0         NaN  
4                 1000.0         NaN  
...                  ...         ...  
2453530           1000.0         NaN  
2453531             20.0         NaN  
2453532           1000.0         NaN  
2453533             50.0         NaN  
2453534           1000.0         NaN  

[2453535 rows x 11 columns]

In [5]:
locations_df = pd.read_csv('GeoLite2-City-Locations-en.csv')
locations_df

geoname_id locale_code continent_code continent_name country_iso_code  \
0            5819          en             EU         Europe               CY   
1           18918          en             EU         Europe               CY   
2           49518          en             AF         Africa               RW   
3           49747          en             AF         Africa               SO   
4           51537          en             AF         Africa               SO   
...           ...         ...            ...            ...              ...   
85970    12747730          en             SA  South America               AR   
85971    12747765          en             SA  South America               AR   
85972    12747769          en             SA  South America               AR   
85973    12747840          en             SA  South America               AR   
85974    12750606          en             AS           Asia               MY   

      country_name subdivision_1_iso_code subdivision_1_name  \
0           Cyprus                     02  Limassol District   
1           Cyprus                     04        Ammochostos   
2           Rwanda                    NaN                NaN   
3          Somalia                     BK             Bakool   
4          Somalia                    NaN                NaN   
...            ...                    ...                ...   
85970    Argentina                      H              Chaco   
85971    Argentina                      H              Chaco   
85972    Argentina                      H              Chaco   
85973    Argentina                      H              Chaco   
85974     Malaysia                     14       Kuala Lumpur   

      subdivision_2_iso_code subdivision_2_name    city_name  metro_code  \
0                        NaN                NaN        Soúni         NaN   
1                        NaN                NaN     Protaras         NaN   
2                        NaN                NaN          NaN         NaN   
3                        NaN                NaN        Oddur         NaN   
4                        NaN                NaN          NaN         NaN   
...                      ...                ...          ...         ...   
85970                    NaN                NaN    La Picada         NaN   
85971                    NaN                NaN   Las Flores         NaN   
85972                    NaN                NaN     El Nandu         NaN   
85973                    NaN                NaN   La Matanza         NaN   
85974                    NaN                NaN  Wangsa Maju         NaN   

                       time_zone  is_in_european_union  
0                   Asia/Nicosia                     1  
1                 Asia/Famagusta                     1  
2                  Africa/Kigali                     0  
3               Africa/Mogadishu                     0  
4               Africa/Mogadishu                     0  
...                          ...                   ...  
85970  America/Argentina/Cordoba                     0  
85971  America/Argentina/Cordoba                     0  
85972  America/Argentina/Cordoba                     0  
85973  America/Argentina/Cordoba                     0  
85974          Asia/Kuala_Lumpur                     0  

[85975 rows x 14 columns]

In [7]:
robi_asn = asn_df[asn_df['autonomous_system_organization'] == 'TM International Bangladesh']
robi_asn

network  autonomous_system_number  \
33355    36.255.80.0/22                     24432   
46383       42.0.4.0/22                     24432   
75368   58.145.184.0/21                     24432   
185627  103.25.248.0/22                     24432   
186065  103.31.153.0/24                     24432   
186066  103.31.154.0/23                     24432   
188589   103.73.46.0/24                     24432   
203960  103.242.20.0/22                     24432   
428942   202.134.8.0/21                     24432   
430278  202.181.18.0/24                     24432   
431646  203.13.162.0/23                     24432   

       autonomous_system_organization  
33355     TM International Bangladesh  
46383     TM International Bangladesh  
75368     TM International Bangladesh  
185627    TM International Bangladesh  
186065    TM International Bangladesh  
186066    TM International Bangladesh  
188589    TM International Bangladesh  
203960    TM International Bangladesh  
428942    TM International Bangladesh  
430278    TM International Bangladesh  
431646    TM International Bangladesh

In [9]:
latlng_df = city_df[city_df['network'].isin(robi_asn['network'])]
latlng_df

network  geoname_id  registered_country_geoname_id  \
282622    36.255.80.0/22   1210997.0                      1210997.0   
373550       42.0.4.0/22   1210997.0                      1210997.0   
517859   58.145.184.0/21   1205733.0                      1210997.0   
1288741  103.31.153.0/24   1185116.0                      1210997.0   
1288742  103.31.154.0/23   1185116.0                      1210997.0   
1293489   103.73.46.0/24   1210997.0                      1210997.0   
1318243  103.242.20.0/22   1205733.0                      1210997.0   
2200242  202.181.18.0/24   1210997.0                      1210997.0   
2202851  203.13.162.0/23   1210997.0                      1210997.0   

         represented_country_geoname_id  is_anonymous_proxy  \
282622                              NaN                   0   
373550                              NaN                   0   
517859                              NaN                   0   
1288741                             NaN                   0   
1288742                             NaN                   0   
1293489                             NaN                   0   
1318243                             NaN                   0   
2200242                             NaN                   0   
2202851                             NaN                   0   

         is_satellite_provider postal_code  latitude  longitude  \
282622                       0         NaN   23.7018    90.3742   
373550                       0         NaN   23.7018    90.3742   
517859                       0        4203   22.3919    91.8335   
1288741                      0        2400   24.8629    90.8344   
1288742                      0        2400   24.8629    90.8344   
1293489                      0         NaN   23.7018    90.3742   
1318243                      0        4000   22.3468    91.8300   
2200242                      0         NaN   23.7018    90.3742   
2202851                      0         NaN   23.7018    90.3742   

         accuracy_radius  is_anycast  
282622             200.0         NaN  
373550            1000.0         NaN  
517859            1000.0         NaN  
1288741            100.0         NaN  
1288742            100.0         NaN  
1293489           1000.0         NaN  
1318243           1000.0         NaN  
2200242            200.0         NaN  
2202851            200.0         NaN

In [10]:
latlng_df['latitude'].nunique()

4

In [11]:
!wget -nc https://d2koia3g127518.cloudfront.net/final_export/MLS-full-cell-export-final.csv.gz

--2024-05-24 17:52:22--  https://d2koia3g127518.cloudfront.net/final_export/MLS-full-cell-export-final.csv.gz
Resolving d2koia3g127518.cloudfront.net (d2koia3g127518.cloudfront.net)... 65.9.108.125, 65.9.108.170, 65.9.108.137, ...
Connecting to d2koia3g127518.cloudfront.net (d2koia3g127518.cloudfront.net)|65.9.108.125|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1565271921 (1.5G) [application/x-gzip]
Saving to: ‘MLS-full-cell-export-final.csv.gz’

MLS-full-cell-expor 100%[===================>]   1.46G  20.7MB/s    in 76s     

2024-05-24 17:53:39 (19.6 MB/s) - ‘MLS-full-cell-export-final.csv.gz’ saved [1565271921/1565271921]



In [17]:
!awk '$3=="kB"{$2=$2/1024^2;$3="GB";} 1' /proc/meminfo | column -t

MemTotal:           123.791      GB
MemFree:            101.668      GB
MemAvailable:       108.92       GB
Buffers:            0.0682869    GB
Cached:             8.04576      GB
SwapCached:         0            GB
Active:             13.0049      GB
Inactive:           7.84785      GB
Active(anon):       12.7574      GB
Inactive(anon):     0            GB
Active(file):       0.247513     GB
Inactive(file):     7.84785      GB
Unevictable:        0.0352745    GB
Mlocked:            0.0260162    GB
SwapTotal:          0            GB
SwapFree:           0            GB
Zswap:              0            GB
Zswapped:           0            GB
Dirty:              3.43323e-05  GB
Writeback:          0            GB
AnonPages:          12.7716      GB
Mapped:             0.193966     GB
Shmem:              0.00287247   GB
KReclaimable:       0.285931     GB
Slab:               0.406624     GB
SReclaimable:       0.285931     GB
SUnreclaim:         0.120693     GB
KernelStack:        0.006347

In [15]:
mls_df = pd.read_csv('MLS-full-cell-export-final.csv')

In [16]:
mls_df

radio  mcc  net   area      cell   unit        lon        lat  range  \
0          GSM  202    0     25     12852    NaN  23.800216  37.994988      0   
1          GSM  202    0     27      5371    NaN  23.825965  38.064419    349   
2          GSM  202    0     27     18263    NaN  23.791401  38.054497     57   
3          GSM  202    0     27     18361    NaN  23.778501  38.133703     36   
4          GSM  202    0     27     53076    NaN  23.771893  38.020783    251   
...        ...  ...  ...    ...       ...    ...        ...        ...    ...   
64751918  UMTS  748   85   9031    198577   96.0 -57.851485 -34.472280    197   
64751919  UMTS  748   85   9031    198861   72.0 -57.367586 -33.871296   1188   
64751920  UMTS  748   85   9055    330315  273.0 -53.540952 -34.044158      0   
64751921  UMTS  748   85   9060    265167  235.0 -58.388812 -33.066637     85   
64751922  UMTS  748  115  19730  69002325  264.0 -57.850697 -34.472084    149   

          samples  changeable     created     updated  averageSignal  
0               1           1  1657960739  1657960739            NaN  
1              16           1  1705502523  1705503521            NaN  
2              10           1  1659027120  1659027313            NaN  
3              10           1  1685540551  1685540680            NaN  
4              22           1  1673005956  1673006345            NaN  
...           ...         ...         ...         ...            ...  
64751918        6           1  1457705614  1457745890            NaN  
64751919      150           1  1467119536  1473348442            NaN  
64751920        1           1  1494419769  1494419769            NaN  
64751921        4           1  1453151407  1453151407            NaN  
64751922        6           1  1438569900  1438580655            NaN  

[64751923 rows x 14 columns]

In [3]:
# bd_towers = mls_df[mls_df['mcc'] == 470]
bd_towers = pd.read_csv('bd_towers.csv')
bd_towers

radio  mcc  net   area      cell   unit        lon        lat  range  \
0        GSM  470    1      1      1592    NaN  90.935975  22.977530      0   
1        GSM  470    1      1      1635    NaN  91.964853  24.924374    362   
2        GSM  470    1     15     13882    NaN  91.889698  25.117348   5287   
3        GSM  470    1     15     13883    NaN  91.890922  25.116090   5143   
4        GSM  470    1     19     10336    NaN  90.401533  23.909506     51   
...      ...  ...  ...    ...       ...    ...        ...        ...    ...   
230675  UMTS  470   85  40924  71970037  149.0  90.413967  23.736223    138   
230676  UMTS  470   85  40924  71979049  370.0  90.410346  23.737964     45   
230677  UMTS  470   85  40924  71979181  300.0  90.420372  23.732364     49   
230678  UMTS  470   85  40924  71989049  378.0  90.410287  23.738236     49   
230679  UMTS  470   85  40933  72054865  309.0  90.420581  23.718381     37   

        samples  changeable     created     updated  averageSignal  
0             1           1  1514560825  1581072680            NaN  
1            11           1  1514560825  1514560825            NaN  
2            16           1  1436697491  1446822932            NaN  
3            48           1  1436697491  1446822701            NaN  
4             4           1  1537090538  1537090544            NaN  
...         ...         ...         ...         ...            ...  
230675       10           1  1437039918  1439262719            NaN  
230676        2           1  1436759118  1436759132            NaN  
230677        4           1  1438969816  1438969816            NaN  
230678        2           1  1436759118  1439262719            NaN  
230679        5           1  1436759118  1439262719            NaN  

[230680 rows x 14 columns]

In [19]:
bd_towers.to_csv('bd_towers.csv', index=False)

In [24]:
robi_latlng = bd_towers[((bd_towers.net == 2) | (bd_towers.net == 7)) & (bd_towers.samples > 320)]
gp_latlng = bd_towers[(bd_towers.net == 1) & (bd_towers.samples > 90)]
bl_latlng = bd_towers[(bd_towers.net == 3) & (bd_towers.samples > 90)]
tt_latlng = bd_towers[(bd_towers.net == 4) & (bd_towers.samples > 105)]
print("Number of Robi and Airtel towers:", len(robi_latlng))
print("Number of Grameenphone towers:", len(gp_latlng))
print("Number of Banglalink towers:", len(bl_latlng))
print("Number of Teletalk towers:", len(tt_latlng))
robi_latlng

Number of Robi and Airtel towers: 2423
Number of Grameenphone towers: 12079
Number of Banglalink towers: 4036
Number of Teletalk towers: 3315


radio  mcc  net   area      cell   unit        lon        lat  range  \
36357    GSM  470    2      1     18652    NaN  90.405118  23.800695   6440   
36361    GSM  470    2      1     65004    NaN  90.414980  23.825597   3704   
36362    GSM  470    2      1     65005    NaN  90.417410  23.826832   4193   
36363    GSM  470    2      1     65006    NaN  90.416215  23.831014    441   
36367    GSM  470    2      1     65016    NaN  90.422376  23.804998   2652   
...      ...  ...  ...    ...       ...    ...        ...        ...    ...   
230111  UMTS  470    7  51317  71598314    NaN  90.726255  23.149195  11102   
230112  UMTS  470    7  51317  71598319    NaN  90.769378  23.038272   5338   
230130  UMTS  470    7  51317  71598528  377.0  91.539234  22.885921  12308   
230215  UMTS  470    7  60322  71779159  112.0  89.238262  24.008602    701   
230419  UMTS  470    7  63903  69030021  488.0  90.384982  23.789051    678   

        samples  changeable     created     updated  averageSignal  
36357       847           1  1409461492  1432309560            NaN  
36361      1059           1  1407637579  1435839795            NaN  
36362       417           1  1408782008  1430488544            NaN  
36363       403           1  1408782010  1430488544            NaN  
36367       327           1  1414434292  1430488544            NaN  
...         ...         ...         ...         ...            ...  
230111      575           1  1426255471  1431111767            NaN  
230112      748           1  1429982229  1434663644            NaN  
230130     2307           1  1430436408  1463131805            NaN  
230215      686           1  1477045600  1496835423            NaN  
230419      527           1  1473495094  1479405144            NaN  

[2423 rows x 14 columns]

In [7]:
def plotDot(point, color):
    ''' Function to create a CircleMarker and add it to your map.
        - point: a series that contains latitude and longitude
        - color: color for the circle marker
    '''
    folium.CircleMarker(location=[point.lat, point.lon],
                        radius=1,
                        weight=5,
                        color=color,
                        fill=True,
                        fill_opacity=0.4).add_to(this_map)

In [8]:
# Create a map centered around a point (update the location based on your area of interest)
this_map = folium.Map(location=[23.6850, 90.3563], prefer_canvas=True, zoom_start=7)

# Plot each operator with a different color
gp_latlng.apply(lambda row: plotDot(row, 'blue'), axis=1)
robi_latlng.apply(lambda row: plotDot(row, 'red'), axis=1)
bl_latlng.apply(lambda row: plotDot(row, 'green'), axis=1)
tt_latlng.apply(lambda row: plotDot(row, 'purple'), axis=1)

# Fit the map to the bounds
this_map.fit_bounds(this_map.get_bounds())

# Save the map to an HTML file
this_map.save('multi_operator_map.html')

this_map

In [25]:
gp_latlng.to_csv('gp_towers.csv', index=False)
robi_latlng.to_csv('robi_towers.csv', index=False)
bl_latlng.to_csv('bl_towers.csv', index=False)
tt_latlng.to_csv('tt_towers.csv', index=False)